## Feature Engineering - Map Education - Step 2

### Imports

In [ ]:
from pyspark.sql.types import *
from pyspark.sql import functions as F

### Load Job Postings(/Skills) data

In [ ]:
n_samples = 24
sample_size = 1000
dir_path = "dbfs:/user_data/g37/"
i=0
file_path = dir_path + f"skills_true_narrowed_{sample_size}_{i}.parquet"
pdf = spark.read.parquet(file_path, header = True, mode="PERMISSIVE",columnNameOfCorruptRecord="_corrupt_record")
for i in range(1, n_samples):
    if i not in [15]:
        file_path = dir_path + f"skills_true_narrowed_{sample_size}_{i}.parquet"
        sdf = spark.read.parquet(file_path, header = True, mode="PERMISSIVE",columnNameOfCorruptRecord="_corrupt_record")
        pdf = pdf.union(sdf)

### Restructuring Job Posting

In [ ]:
required_experience_item_array = ArrayType(StructType([StructField('experience_in_field', StringType(), True), StructField('minimal_years_of_experience_in_the_field', StringType(), True)]), True)

required_education_item_array = ArrayType(StructType([StructField('type_of_education', StringType(), True), StructField('education_in_field', StringType(), True)]), True)

extracted = StructType() \
    .add("required_education_item_array", required_education_item_array, True) \
        .add('required_experience_item_array', required_experience_item_array, True)

In [ ]:
structed = pdf.dropna(subset="job_summary_processed").withColumn("job_summary_processed", F.udf(lambda x: eval(x),returnType=extracted)("job_summary_processed")).withColumn("id", F.monotonically_increasing_id())

In [ ]:
res = structed.select(
    "id",
    "position",
    "narrow_position",
    F.udf(lambda x: x.split(", ") if x is not None else None, returnType=ArrayType(StringType()))("skills").alias("skills"),
    "job_summary",
    F.col("job_summary_processed.required_education_item_array.type_of_education").alias("education_degree"),
    F.col("job_summary_processed.required_education_item_array.type_of_education").alias("education_degree_gen"),
    F.col("job_summary_processed.required_education_item_array.education_in_field").alias("education_field"),
    F.col("job_summary_processed.required_education_item_array.education_in_field").alias("education_fields_gen"),
    F.col("job_summary_processed.required_experience_item_array.experience_in_field").alias("experience_titles"),
    F.col("job_summary_processed.required_experience_item_array.experience_in_field").alias("experience_titles_gen"),
    F.col("job_summary_processed.required_experience_item_array.minimal_years_of_experience_in_the_field").astype(ArrayType(FloatType())).alias("experience_durations"),
    F.col("job_summary_processed.required_experience_item_array.minimal_years_of_experience_in_the_field").astype(ArrayType(FloatType())).alias("experience_durations_gen")
)

### Converting degree column

In [ ]:
respd_long = res.select("id", F.explode("education_degree").alias("d")).groupBy("d").count().sort(F.asc("count")).collect()
klong = list({i.asDict()["d"]: i.asDict()["count"] for i in respd_long}.keys())

conv_dict = {
    "High School Diploma": [k for k in klong if k is not None and len(k) > 0 and "high" in k.lower()],
    "Certification": [k for k in klong if k is not None and len(k) > 0 and "cert" in k.lower()],
    "Diploma": [k for k in klong if k is not None and len(k) > 0 and "dipl" in k.lower()], 
    "Master's Degree": [k for k in klong if k is not None and len(k) >0 and ((k[0] == "M" and k.upper() == k) or "master" in k.lower())],
    "Bachelor's Degree": [k for k in klong if k is not None and len(k) >0 and ((k[0] == "B" and k.upper() == k) or "bachelor" in k.lower() or "undergraduate" in k.lower())],
    "Associate's Degree": [k for k in klong if k is not None and len(k) >0 and ((k[0] == "A" and k.upper() == k) or "associate" in k.lower())],
    "Doctoral Degree": [k for k in klong if k is not None and len(k) >0 and ( "phd" in k.strip(".").lower() or "doct" in k.strip(".").lower())]
}
conv_keys = ["High School Diploma", "Certification", "Diploma", "Associate's Degree", "Bachelor's Degree", "Master's Degree", "Doctoral Degree"]

def conv_deg(degs):
    if degs == None:
        return []
    new_degs = []
    for deg in degs:
        found = False
        for k in conv_keys:
            if deg in conv_dict[k]:
                new_degs.append(k)
                found = True
                break
        if not found:
            new_degs.append(deg)
    return new_degs
conv_deg_udf = F.udf(conv_deg, returnType=ArrayType(StringType()))

In [ ]:
degrees = res.withColumn("education_degree", conv_deg_udf("education_degree"))
degrees.display()

id position narrow_position skills job_summary education_degree education_degree_gen education_field education_fields_gen experience_titles experience_titles_gen experience_durations experience_durations_gen 0 Tasting Room Operations Manager Gas Operations Manager List(Sales Management, Budget Management, Profitability Analysis, Strategic Planning, Team Goal Setting, Event Planning, Sales Forecasting, Customer Needs Analysis, Market Trend Analysis, Community Engagement, Ownership Mindset, Business Improvement, Bachelor's Degree (Business Marketing Communications), 57 years experience (related field), Budget Development, P&L Management, Team Management, Clean Driving Record, Lifting (50 lbs), Traveling, Supervisory Responsibilities) Summary:
The Tasting Room Operations Manager at Miller Family Wine Company is responsible for overseeing the sales activities and operations of all Tasting Rooms and Wine Clubs. This role involves strategic planning, budget management, and ensuring profitability while maintaining a high level of customer engagement and satisfaction.
Essential Functions:
1.
Financial Oversight:
·      Oversee and understand Tasting Room and Wine Club P+L.
·      Track and implement tasting room budgets.
·      Analyze COGS and margins, implementing a strategic profitability model.
2.
Strategic Planning:
·      Develop and implement strategic sales plans aligned with corporate goals.
·      Create team goals that support overall corporate objectives.
·      Collaborate with Events Coordinator on to create ongoing events, new initiatives, and programming.
·      Understand and provide recommended avenues for Marketing initiatives to drive brand awareness and business strategy
3.
Sales and Forecasting:
·      Work closely with demand planning and sales channels to develop accurate annual forecasts.
·      Align sales goals, strategy, and vintage release schedules.
·      Monitor and manage discounting allowances.
4.
Operational Efficiency:
·      Align cross-departmentally to create efficiencies.
·      Review daily sales numbers, foot traffic, and conversion rates for effective business management.
·      Analyze product margin and profitability to provide strategic solutions.
5.
Team Management:
·      Supervise Tasting Room leads, Event Coordinator, and Wine Club Manager.
·      Support and oversee Tasting Room day-to-day initiatives as needed
·      Provide training, performance evaluations, and foster a culture of continuous improvement.
6.
Market Analysis and Community Engagement:
·      Stay informed about market trends and analyze customer needs, price schedules, and discount rates.
·      Represent the company at trade association meetings to promote products and brands.
·      Cultivate relationships within the community to drive engagement and foot traffic.
7.
Ownership Mentality:
·      Instill a sense of "ownership" over the success of the business, brands, and position within the organization.
·      Constantly seek opportunities for learning and improving the current state of the business for short and long-term success.
Job Requirements:
Duties and responsibilities may be added, deleted, or changed at any time at the discretion of management, formally or informally, either verbally or in writing.
Education and Experience:
Bachelor’s Degree in Business, Marketing, Communications, or a related field, or equivalent of 5-7 years of experience with some education.
Required Skills:
Three or more years of proven success in similar role
·        Strong skills in budget development, P+L management and oversight
·        Proficiency in team management
·        Clean driving record
Physical Demands:
Must be able to occasionally lift 50 lbs.
Ability to travel/drive between Tasting Rooms effectively
Supervisory Responsibilities:
Directly supervises 3 or more employees.
Carries out supervisory responsibilities in accordance with the organization's policies and applicable laws.
Responsibilities include interviewing, hi

### Saving

In [ ]:
degrees.write.parquet("dbfs:/user_data/g37/skills_and_degrees_true_narroweddd.parquet")
degrees.count()

Out[297]: 22338

________________________________________

### Loading Profiles data

In [ ]:
dir_path = "dbfs:/user_data/g37/"
file_name = "profiles_data_for_project.parquet"
file_path = dir_path + file_name
profiles = spark.read.parquet(file_path, header = True)

### mapping education degree column

In [ ]:
import re
degree_types = {
        "AA": ["Associate of Arts"],
        "AAS": ["Associate of Applied Science"],
        "AS": ["Associate of Science"],
        "BA": ["Bachelor of Arts"],
        "BAA": ["Bachelor of Applied Arts"],
        "BS": ["Bachelor of Science"],
        "BAS": ["Bachelor of Applied Science"],
        "B.Arch.": ["Bachelor of Architecture"],
        "BBA": ["Bachelor of Business Administration"],
        "BFA": ["Bachelor of Fine Arts"],
        "BSN": ["Bachelor of Science in Nursing"],
        "MA": ["Master of Arts"],
        "MS": ["Master of Science"],
        "MBA": ["Master of Business Administration"],
        "M.Ed.": ["Master of Education"],
        "MFA": ["Master of Fine Arts"],
        "LL.M.": ["Master of Laws"],
        "MPA": ["Master of Public Administration"],
        "MPH": ["Master of Public Health"],
        "MPP": ["Master of Public Policy"],
        "MSN": ["Master of Science in Nursing"],
        "MSW": ["Master of Social Work"],
        "Ph.D.": ["Doctor of Philosophy"],
        "DBA": ["Doctor of Business Administration"],
        "Ed.D.": ["Doctor of Education"],
        "MD": ["Doctor of Medicine"],
        "DNP": ["Doctor of Nursing Practice"],
        "Pharm.D.": ["Doctor of Pharmacy"],
        "Psy.D.": ["Doctor of Psychology"],
        "JD": ["Juris Doctor"],
        "Certificate": ["Certificate"],
        "Course": ["Course"],
        "CRS": ["CRS"],
        "Diploma": ["Diploma"],
        "High School Diploma": ["High School"]
    }

    
def convert_degree_type(input_string):
    # Dictionary mapping degree abbreviations to full names
    if input_string == None:
        return None
    d = input_string.replace(".", "").lower().split()
    # Iterate through degree types to find matches
    for abr, full in degree_types.items():
        if abr.replace(".", "").lower() in d or full[0].replace(".", "").lower() in d:
            return abr
    
    # Return None if no match found
    return None
cdtudf = F.udf(convert_degree_type)

In [ ]:
res = profiles.select("*", F.explode("education").alias("edu_item"))
res = res.select("*", cdtudf(F.col("edu_item.degree")).alias("dp"), F.col("edu_item.field").alias("field"))

In [ ]:
res_grouped = res.dropna(subset="dp").groupby("id").agg(F.collect_list("dp").alias("dp_list"))

### Saving degree column

In [ ]:
res_grouped.write.parquet("dbfs:/user_data/g37/profiles_education_fixed.parquet")

### joining with original

In [ ]:
dir_path = "dbfs:/user_data/g37/"
file_name = "profiles_education_fixed.parquet"
file_path = dir_path + file_name
profiles_education_fixed = spark.read.parquet(file_path, header = True)

In [ ]:
new_profiles = profiles.join(profiles_education_fixed, on='id', how='inner')

### Saving new Profiles

In [ ]:
new_profiles.write.parquet("dbfs:/user_data/g37/profiles_new.parquet")